Q2-3

Import

In [70]:
import pandas as pd
import numpy as  np
from sklearn.preprocessing import LabelEncoder
from sklearn.linear_model import LogisticRegression
from sklearn import metrics
from sklearn.metrics import confusion_matrix
import csv
import warnings

Data import

In [71]:
labelencoder = LabelEncoder()
pd.set_option ( "display.max_rows", 20000 )
pd.set_option ( "display.max_columns", 20 )
usecols_data = ['satisfaction_level','last_evaluation','number_project','average_montly_hours','time_spend_company','Work_accident','promotion_last_5years','sales','salary']
df_data_all = pd.read_csv( r'HW2_data/HW2_hr-analytics_train.csv' )
print ( "Number of NaN in the Data" )
print ( df_data_all.isna().sum() )
df_data = pd.read_csv( r'HW2_data/HW2_hr-analytics_train.csv' , usecols = usecols_data )
df_label = pd.read_csv( r'HW2_data/HW2_hr-analytics_train.csv' , usecols = ['left'] )
df_test = pd.read_csv( r'HW2_data/HW2_hr-analytics_test.csv' )

Number of NaN in the Data
satisfaction_level       0
last_evaluation          0
number_project           0
average_montly_hours     0
time_spend_company       0
Work_accident            0
promotion_last_5years    0
sales                    0
salary                   0
left                     0
dtype: int64


In [89]:
df_data_not_number = df_data_all.select_dtypes(include = ["object" ])
df_data_not_number = df_data_not_number.columns.tolist()
print ( "非數字的資料" )
for i in df_data_not_number:
    print ( i )

非數字的資料
sales
salary


Data PreProcessing and Encode (編碼與填補缺失值)

In [72]:
for i in usecols_data:
    df_data[i] = labelencoder.fit_transform(df_data[i])
for i in usecols_data:
    df_test[i] = labelencoder.fit_transform(df_test[i])
df_data_nmp=df_data.to_numpy()
df_label_nmp=df_label.to_numpy()
data_splitted_arr_1 , data_splitted_arr_2 = np.vsplit(df_data_nmp, 2)
label_splitted_arr_1 , label_splitted_arr_2 = np.vsplit(df_label_nmp, 2)

label_splitted_arr_1 = label_splitted_arr_1.ravel()
label_splitted_arr_2 = label_splitted_arr_2.ravel()

data_splitted_arr_1 = pd.DataFrame(data = data_splitted_arr_1 , columns = usecols_data )
data_splitted_arr_2 = pd.DataFrame(data = data_splitted_arr_2 , columns = usecols_data )

Train Model - Decision Tree

In [73]:
from sklearn.tree import DecisionTreeClassifier, export_text, plot_tree
import matplotlib.pyplot as plt
from sklearn.metrics import classification_report,confusion_matrix
dtree = DecisionTreeClassifier()
dtree.fit(data_splitted_arr_1,label_splitted_arr_1)
pred = dtree.predict(data_splitted_arr_2)
print ( "Decision Tree" ) 
print("Accuracy:" ,metrics.accuracy_score(label_splitted_arr_2, pred))
print("Precision:",metrics.precision_score(label_splitted_arr_2, pred))
print("Recall:" ,metrics.recall_score(label_splitted_arr_2, pred))
matrix = confusion_matrix(label_splitted_arr_2,pred)
print ( "Confusion Matrix" )
print ( matrix )

Decision Tree
Accuracy: 0.9686
Precision: 0.8877463581833762
Recall: 0.975517890772128
Confusion Matrix
[[3807  131]
 [  26 1036]]


印出前兩個最重要的特徵

In [74]:
dtree_importances = dtree.feature_importances_
dtree_indices = np.argsort(dtree_importances)[::-1]
print( "Top 2 most important features:" )
print( f"Feature {usecols_data[dtree_indices[0]]}: Importance Score {dtree_importances[dtree_indices[0]]}" )
print( f"Feature {usecols_data[dtree_indices[1]]}: Importance Score {dtree_importances[dtree_indices[1]]}" )

Top 2 most important features:
Feature satisfaction_level: Importance Score 0.49952910038383513
Feature time_spend_company: Importance Score 0.18676581358477312
Feature last_evaluation: Importance Score 0.12128823515536447


印出決策樹圖

In [75]:
plt.figure(figsize=(200, 200))
plot_tree(dtree,
          filled=True, rounded=True, proportion=True,
          feature_names = usecols_data,
          class_names = ['left','leave'])
plt.savefig('tree.png')

Train Model - Logistic Regression

In [76]:
model = LogisticRegression( max_iter = 500 )

model.fit(data_splitted_arr_1, label_splitted_arr_1)
predictions = model.predict(data_splitted_arr_2)

model.score(data_splitted_arr_1,label_splitted_arr_1)
print ( "Logistic Regression" ) 
print("Accuracy:" ,metrics.accuracy_score(label_splitted_arr_2, predictions))
print("Precision:",metrics.precision_score(label_splitted_arr_2, predictions))
print("Recall:" ,metrics.recall_score(label_splitted_arr_2, predictions))

coef_model = list(model.coef_)
pos_coef = list()
for i in range(len(coef_model[0])):
    if coef_model[0][i] > 0:
        pos_coef.append ( i )

matrix = confusion_matrix(label_splitted_arr_2,predictions)
print ( "Confusion Matrix" )
print ( matrix )


Logistic Regression
Accuracy: 0.7218
Precision: 0.3469767441860465
Recall: 0.3512241054613936
Confusion Matrix
[[3236  702]
 [ 689  373]]


決策樹的準確度大約是96%
邏輯回歸的準確度大約是72%

In [77]:
test_final_predictions = model.predict(df_test)
with open('/Users/jimmywang/Desktop/Jupyter/ML/HW2/HW2_hr-analytics_test_sol_lr.csv', 'w', newline='') as csvfile:
  writer = csv.writer(csvfile)
  writer.writerow(["left"])
  for i in np.nditer(test_final_predictions):
      writer.writerow([i])

In [78]:
dt_final_predictions = dtree.predict(df_test)
with open('/Users/jimmywang/Desktop/Jupyter/ML/HW2/HW2_hr-analytics_test_sol.csv', 'w', newline='') as csvfile:
  writer = csv.writer(csvfile)
  writer.writerow(["left"])
  for i in np.nditer(dt_final_predictions):
      writer.writerow([i])

相關性分析

In [79]:
df_data_all_drop = df_data_all.select_dtypes(include = ["int64", "float64" ])
correlation_matrix = df_data_all_drop.corr()
correlation_with_target = correlation_matrix['left']
print(correlation_with_target.abs().sort_values(ascending=False))

left                     1.000000
satisfaction_level       0.389721
Work_accident            0.158327
time_spend_company       0.138764
average_montly_hours     0.069911
promotion_last_5years    0.064861
number_project           0.023949
last_evaluation          0.008456
Name: left, dtype: float64


上面結果可以知道各項特徵與離職率的相關性不高，用決策樹這樣的分類模型會比邏輯回歸的效果更好。